# Useful links

*   [SecML](https://github.com/pralab/secml)
*   [SecML (doc)](https://secml.readthedocs.io/en/v0.15/)
*   [Robust Art](https://github.com/Trusted-AI/adversarial-robustness-toolbox)
*   [Metriche](https://github.com/ryderling/DEEPSEC/blob/master/Evaluations/AttackEvaluations.py#L315)





In [1]:
# !git clone https://github.com/Trusted-AI/adversarial-robustness-toolbox.git
!pip install adversarial-robustness-toolbox
!pip install
!pip install multiprocess
#!pip install imagenet-c

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 15.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 30.5/30.5 MB 52.1 MB/s eta 0:00:00
  Attempting uninstall: scikit-learn
    Found existing installation: scikit-learn 1.2.2
    Uninstalling scikit-learn-1.2.2:
      Successfully uninstalled scikit-learn-1.2.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
bigframes 0.20.1 requires scikit-learn>=1.2.2, but you have scikit-learn 1.1.3 which is incompatible.


In [20]:
"""
The script demonstrates a simple example of using ART with PyTorch. The example train a small model on the MNIST dataset
and creates adversarial examples using the Fast Gradient Sign Method. Here we use the ART classifier to train the model,
it would also be possible to provide a pretrained model to the ART classifier.
The parameters are chosen for reduced computational requirements of the script and not optimised for accuracy.
"""
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import numpy as np
import copy
import multiprocess

from art.attacks.evasion import FastGradientMethod, ProjectedGradientDescent, CarliniLInfMethod, ZooAttack, PixelAttack, AutoAttack
from art.estimators.classification import PyTorchClassifier
from art.utils import load_mnist

In [3]:
# Step 0: Define the neural network model, return logits instead of activation in forward method


class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.conv_1 = nn.Conv2d(in_channels=1, out_channels=4, kernel_size=5, stride=1)
        self.conv_2 = nn.Conv2d(in_channels=4, out_channels=10, kernel_size=5, stride=1)
        self.fc_1 = nn.Linear(in_features=4 * 4 * 10, out_features=100)
        self.fc_2 = nn.Linear(in_features=100, out_features=10)

    def forward(self, x):
        x = F.relu(self.conv_1(x))
        x = F.max_pool2d(x, 2, 2)
        x = F.relu(self.conv_2(x))
        x = F.max_pool2d(x, 2, 2)
        x = x.view(-1, 4 * 4 * 10)
        x = F.relu(self.fc_1(x))
        x = self.fc_2(x)
        return x

In [4]:
# Step 1: Load the MNIST dataset

(x_train, y_train), (x_test, y_test), min_pixel_value, max_pixel_value = load_mnist()

# Step 1a: Swap axes to PyTorch's NCHW format

x_train = np.transpose(x_train, (0, 3, 1, 2)).astype(np.float32)
x_test = np.transpose(x_test, (0, 3, 1, 2)).astype(np.float32)

# Step 2: Create the model

model = Net()

# Step 2a: Define the loss function and the optimizer

criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.01)

# Step 3: Create the ART classifier

classifier = PyTorchClassifier(
    model=model,
    clip_values=(min_pixel_value, max_pixel_value),
    loss=criterion,
    optimizer=optimizer,
    input_shape=(1, 28, 28),
    nb_classes=10,
)

In [5]:
# Step 4: Train the ART classifier

classifier.fit(x_train, y_train, batch_size=64, nb_epochs=3)

In [6]:
# Step 5: Evaluate the ART classifier on benign test examples

predictions = classifier.predict(x_test)
accuracy = np.sum(np.argmax(predictions, axis=1) == np.argmax(y_test, axis=1)) / len(y_test)
print("Accuracy on benign test examples: {}%".format(accuracy * 100))

Accuracy on benign test examples: 98.07000000000001%


# FGSM

In [ ]:
# Step 6: Generate adversarial test examples
attack = FastGradientMethod(estimator=copy.copy(classifier), eps=0.2)
x_test_adv = attack.generate(x=x_test)

# Step 7: Evaluate the ART classifier on adversarial test examples

predictions = classifier.predict(x_test_adv)
accuracy = np.sum(np.argmax(predictions, axis=1) == np.argmax(y_test, axis=1)) / len(y_test)
print("Accuracy on adversarial test examples: {}%".format(accuracy * 100))

Accuracy on adversarial test examples: 24.79%


# PGD

In [ ]:
# Step 6: Generate adversarial test examples
attack = ProjectedGradientDescent(estimator=copy.copy(classifier), norm=2, eps=0.5, eps_step=0.2)
x_test_adv = attack.generate(x=x_test)

# Step 7: Evaluate the ART classifier on adversarial test examples

predictions = classifier.predict(x_test_adv)
accuracy = np.sum(np.argmax(predictions, axis=1) == np.argmax(y_test, axis=1)) / len(y_test)
print("Accuracy on adversarial test examples: {}%".format(accuracy * 100))

In [ ]:
# Step 6: Generate adversarial test examples
attack = ProjectedGradientDescent(estimator=copy.copy(classifier), norm=np.inf, eps=0.5, eps_step=0.2)
x_test_adv = attack.generate(x=x_test)

# Step 7: Evaluate the ART classifier on adversarial test examples

predictions = classifier.predict(x_test_adv)
accuracy = np.sum(np.argmax(predictions, axis=1) == np.argmax(y_test, axis=1)) / len(y_test)
print("Accuracy on adversarial test examples: {}%".format(accuracy * 100))

PGD - Batches:   0%|          | 0/313 [00:00<?, ?it/s]

Accuracy on adversarial test examples: 0.97%


# C&W

In [ ]:
# Step 6: Generate adversarial test examples
attack = CarliniL0Method(classifier=copy.copy(classifier))
x_test_adv = attack.generate(x=x_test)

# Step 7: Evaluate the ART classifier on adversarial test examples

predictions = classifier.predict(x_test_adv)
accuracy = np.sum(np.argmax(predictions, axis=1) == np.argmax(y_test, axis=1)) / len(y_test)
print("Accuracy on adversarial test examples: {}%".format(accuracy * 100))

In [ ]:
# Step 6: Generate adversarial test examples
attack = CarliniL2Method(classifier=copy.copy(classifier))
x_test_adv = attack.generate(x=x_test)

# Step 7: Evaluate the ART classifier on adversarial test examples

predictions = classifier.predict(x_test_adv)
accuracy = np.sum(np.argmax(predictions, axis=1) == np.argmax(y_test, axis=1)) / len(y_test)
print("Accuracy on adversarial test examples: {}%".format(accuracy * 100))

In [ ]:
# Step 6: Generate adversarial test examples
attack = CarliniLInfMethod(classifier=copy.copy(classifier))
x_test_adv = attack.generate(x=x_test)

# Step 7: Evaluate the ART classifier on adversarial test examples

predictions = classifier.predict(x_test_adv)
accuracy = np.sum(np.argmax(predictions, axis=1) == np.argmax(y_test, axis=1)) / len(y_test)
print("Accuracy on adversarial test examples: {}%".format(accuracy * 100))

C&W L_inf:   0%|          | 0/10000 [00:00<?, ?it/s]

# One pixel

In [ ]:
# Step 6: Generate adversarial test examples
attack = PixelAttack(classifier=copy.copy(classifier), max_iter=20, verbose=True)
x_test_adv = attack.generate(x=x_test)

# Step 7: Evaluate the ART classifier on adversarial test examples

predictions = classifier.predict(x_test_adv)
accuracy = np.sum(np.argmax(predictions, axis=1) == np.argmax(y_test, axis=1)) / len(y_test)
print("Accuracy on adversarial test examples: {}%".format(accuracy * 100))

# Rumori naturali

In [26]:
# https://github.com/hendrycks/robustness/tree/master/ImageNet-C/imagenet_c

# Non funziona nulla, va reimplementata bene

# from imagenet_c import corrupt

#corrupt(<image>, corruption_number=0)

# Zoo

In [ ]:
# Step 6: Generate adversarial test examples
attack = ZooAttack(classifier=copy.copy(classifier))
x_test_adv = attack.generate(x=x_test)

# Step 7: Evaluate the ART classifier on adversarial test examples

predictions = classifier.predict(x_test_adv)
accuracy = np.sum(np.argmax(predictions, axis=1) == np.argmax(y_test, axis=1)) / len(y_test)
print("Accuracy on adversarial test examples: {}%".format(accuracy * 100))

# AutoAttack

In [21]:
# https://github.com/Trusted-AI/adversarial-robustness-toolbox/blob/main/notebooks/attack_parallel_auto_attack.ipynb

# Step 6: Generate adversarial test examples
attack = AutoAttack(estimator=copy.copy(classifier))
x_test_adv = attack.generate(x=x_test)

# Step 7: Evaluate the ART classifier on adversarial test examples

predictions = classifier.predict(x_test_adv)
accuracy = np.sum(np.argmax(predictions, axis=1) == np.argmax(y_test, axis=1)) / len(y_test)
print("Accuracy on adversarial test examples: {}%".format(accuracy * 100))

AutoPGD - restart:   0%|          | 0/5 [00:00<?, ?it/s]

AutoPGD - batch:   0%|          | 0/313 [00:00<?, ?it/s]

AutoPGD - iteration:   0%|          | 0/100 [00:00<?, ?it/s]

AutoPGD - iteration:   0%|          | 0/100 [00:00<?, ?it/s]

AutoPGD - iteration:   0%|          | 0/100 [00:00<?, ?it/s]

...

AutoPGD - iteration:   0%|          | 0/100 [00:00<?, ?it/s]

AutoPGD - iteration:   0%|          | 0/100 [00:00<?, ?it/s]

AutoPGD - iteration:   0%|          | 0/100 [00:00<?, ?it/s]

AutoPGD - iteration:   0%|          | 0/100 [00:00<?, ?it/s]

Accuracy on adversarial test examples: 0.91%


# Metrics

In [ ]:
# https://github.com/ryderling/DEEPSEC/blob/master/Evaluations/AttackEvaluations.py#L315

In [ ]:
# help function for the Gaussian Blur transformation of images
def gaussian_blur_transform(AdvSample, radius, oriDataset):
    if oriDataset.upper() == 'CIFAR10':
        assert AdvSample.shape == (3, 32, 32)
        sample = np.transpose(np.round(AdvSample * 255), (1, 2, 0))

        image = Image.fromarray(np.uint8(sample))
        gb_image = image.filter(ImageFilter.GaussianBlur(radius=radius))
        gb_image = np.transpose(np.array(gb_image), (2, 0, 1)).astype('float32') / 255.0
        return gb_image

    if oriDataset.upper() == 'MNIST':
        assert AdvSample.shape == (1, 28, 28)
        sample = np.transpose(np.round(AdvSample * 255), (1, 2, 0))
        # for MNIST, there is no RGB
        sample = np.squeeze(sample, axis=2)

        image = Image.fromarray(np.uint8(sample))
        gb_image = image.filter(ImageFilter.GaussianBlur(radius=radius))

        gb_image = np.expand_dims(np.array(gb_image).astype('float32'), axis=0) / 255.0
        return gb_image


# help function for the image compression transformation of images
def image_compress_transform(IndexAdv, AdvSample, dir_name, quality, oriDataset):
    if oriDataset.upper() == 'CIFAR10':
        assert AdvSample.shape == (3, 32, 32)
        sample = np.transpose(np.round(AdvSample * 255), (1, 2, 0))
        image = Image.fromarray(np.uint8(sample))

        saved_adv_image_path = os.path.join(dir_name, '{}th-adv-cifar.png'.format(IndexAdv))
        image.save(saved_adv_image_path)
        output_IC_path = os.path.join(dir_name, '{}th-IC-adv-cifar.jpg'.format(IndexAdv))

        cmd = 'guetzli --quality {} {} {}'.format(quality, saved_adv_image_path, output_IC_path)
        assert os.system(cmd) == 0, 'guetzli tool should be install before, https://github.com/google/guetzli'

        IC_image = Image.open(output_IC_path).convert('RGB')
        IC_image = np.transpose(np.array(IC_image), (2, 0, 1)).astype('float32') / 255.0
        return IC_image

    if oriDataset.upper() == 'MNIST':
        assert AdvSample.shape == (1, 28, 28)
        sample = np.transpose(np.round(AdvSample * 255), (1, 2, 0))
        sample = np.squeeze(sample, axis=2)  # for MNIST, there is no RGB
        image = Image.fromarray(np.uint8(sample), mode='L')

        saved_adv_image_path = os.path.join(dir_name, '{}th-adv-mnist.png'.format(IndexAdv))
        image.save(saved_adv_image_path)
        output_IC_path = os.path.join(dir_name, '{}th-IC-adv-mnist.jpg'.format(IndexAdv))

        cmd = 'guetzli --quality {} {} {}'.format(quality, saved_adv_image_path, output_IC_path)
        assert os.system(cmd) == 0, 'guetzli tool should be install before, https://github.com/google/guetzli'

        IC_image = Image.open(output_IC_path).convert('L')
        IC_image = np.expand_dims(np.array(IC_image).astype('float32'), axis=0) / 255.0
        return IC_image

In [ ]:
# 1 MR:Misclassification Rate
def misclassification_rate(self):

    cnt = 0
    for i in range(len(self.adv_samples)):
        if self.successful(adv_softmax_preds=self.softmax_prediction[i], nature_true_preds=self.labels_samples[i],
                            targeted_preds=self.targets_samples[i], target_flag=self.Targeted):
            cnt += 1
    mr = cnt / len(self.adv_samples)
    print('MR:\t\t{:.1f}%'.format(mr * 100))
    return mr

# 2 ACAC: average confidence of adversarial class
def avg_confidence_adv_class(self):
    cnt = 0
    conf = 0
    for i in range(len(self.adv_samples)):
        if self.successful(adv_softmax_preds=self.softmax_prediction[i], nature_true_preds=self.labels_samples[i],
                            targeted_preds=self.targets_samples[i], target_flag=self.Targeted):
            cnt += 1
            conf += np.max(self.softmax_prediction[i])

    print('ACAC:\t{:.3f}'.format(conf / cnt))
    return conf / cnt

# 3 ACTC: average confidence of true class
def avg_confidence_true_class(self):

    true_labels = np.argmax(self.labels_samples, axis=1)
    cnt = 0
    true_conf = 0
    for i in range(len(self.adv_samples)):
        if self.successful(adv_softmax_preds=self.softmax_prediction[i], nature_true_preds=self.labels_samples[i],
                            targeted_preds=self.targets_samples[i], target_flag=self.Targeted):
            cnt += 1
            true_conf += self.softmax_prediction[i, true_labels[i]]
    print('ACTC:\t{:.3f}'.format(true_conf / cnt))
    return true_conf / cnt

# 4 ALP: Average L_p Distortion
def avg_lp_distortion(self):

    ori_r = np.round(self.nature_samples * 255)
    adv_r = np.round(self.adv_samples * 255)

    NUM_PIXEL = int(np.prod(self.nature_samples.shape[1:]))

    pert = adv_r - ori_r

    dist_l0 = 0
    dist_l2 = 0
    dist_li = 0

    cnt = 0

    for i in range(len(self.adv_samples)):
        if self.successful(adv_softmax_preds=self.softmax_prediction[i], nature_true_preds=self.labels_samples[i],
                            targeted_preds=self.targets_samples[i], target_flag=self.Targeted):
            cnt += 1
            dist_l0 += (np.linalg.norm(np.reshape(pert[i], -1), ord=0) / NUM_PIXEL)
            dist_l2 += np.linalg.norm(np.reshape(self.nature_samples[i] - self.adv_samples[i], -1), ord=2)
            dist_li += np.linalg.norm(np.reshape(self.nature_samples[i] - self.adv_samples[i], -1), ord=np.inf)

    adv_l0 = dist_l0 / cnt
    adv_l2 = dist_l2 / cnt
    adv_li = dist_li / cnt

    print('**ALP:**\n\tL0:\t{:.3f}\n\tL2:\t{:.3f}\n\tLi:\t{:.3f}'.format(adv_l0, adv_l2, adv_li))
    return adv_l0, adv_l2, adv_li

# 4 ASS: Average Structural Similarity
def avg_SSIM(self):

    ori_r_channel = np.transpose(np.round(self.nature_samples * 255), (0, 2, 3, 1)).astype(dtype=np.float32)
    adv_r_channel = np.transpose(np.round(self.adv_samples * 255), (0, 2, 3, 1)).astype(dtype=np.float32)

    totalSSIM = 0
    cnt = 0

    """
    For SSIM function in skimage: http://scikit-image.org/docs/dev/api/skimage.measure.html

    multichannel : bool, optional If True, treat the last dimension of the array as channels. Similarity calculations are done
    independently for each channel then averaged.
    """
    for i in range(len(self.adv_samples)):
        if self.successful(adv_softmax_preds=self.softmax_prediction[i], nature_true_preds=self.labels_samples[i],
                            targeted_preds=self.targets_samples[i], target_flag=self.Targeted):
            cnt += 1
            totalSSIM += SSIM(X=ori_r_channel[i], Y=adv_r_channel[i], multichannel=True)

    print('ASS:\t{:.3f}'.format(totalSSIM / cnt))
    return totalSSIM / cnt


# 7 NTE: Noise Tolerance Estimation
def avg_noise_tolerance_estimation(self):

    nte = 0
    cnt = 0
    for i in range(len(self.adv_samples)):
        if self.successful(adv_softmax_preds=self.softmax_prediction[i], nature_true_preds=self.labels_samples[i],
                            targeted_preds=self.targets_samples[i], target_flag=self.Targeted):
            cnt += 1
            sort_preds = np.sort(self.softmax_prediction[i])
            nte += sort_preds[-1] - sort_preds[-2]

    print('NTE:\t{:.3f}'.format(nte / cnt))
    return nte / cnt

# 8 RGB: Robustness to Gaussian Blur
def robust_gaussian_blur(self, radius=0.5):

    total = 0
    num_gb = 0

    if self.Targeted is True:
        for i in range(len(self.adv_samples)):
            if np.argmax(self.softmax_prediction[i]) == np.argmax(self.targets_samples[i]):
                total += 1
                adv_sample = self.adv_samples[i]
                gb_sample = gaussian_blur_transform(AdvSample=adv_sample, radius=radius, oriDataset=self.dataset)
                gb_pred = predict(model=self.raw_model, samples=np.array([gb_sample]), device=self.device).detach().cpu().numpy()
                if np.argmax(gb_pred) == np.argmax(self.targets_samples[i]):
                    num_gb += 1

    else:
        for i in range(len(self.adv_samples)):
            if np.argmax(self.softmax_prediction[i]) != np.argmax(self.labels_samples[i]):
                total += 1
                adv_sample = self.adv_samples[i]
                gb_sample = gaussian_blur_transform(AdvSample=adv_sample, radius=radius, oriDataset=self.dataset)
                gb_pred = predict(model=self.raw_model, samples=np.array([gb_sample]), device=self.device).detach().cpu().numpy()
                if np.argmax(gb_pred) != np.argmax(self.labels_samples[i]):
                    num_gb += 1

    print('RGB:\t{:.3f}'.format(num_gb / total))
    return num_gb, total, num_gb / total

# 9 RIC: Robustness to Image Compression
def robust_image_compression(self, quality):

    total = 0
    num_ic = 0

    # prepare the save dir for the generated image(png or jpg)
    image_save = os.path.join(self.AdvExamplesDir, 'image')
    if os.path.exists(image_save):
        shutil.rmtree(image_save)
    os.mkdir(image_save)
    print('\nNow, all adversarial examples are saved as PNG and then compressed using *Guetzli* in the {} fold ......\n'.format(image_save))

    if self.Targeted is True:
        for i in range(len(self.adv_samples)):
            if np.argmax(self.softmax_prediction[i]) == np.argmax(self.targets_samples[i]):
                total += 1
                adv_sample = self.adv_samples[i]

                ic_sample = image_compress_transform(IndexAdv=i, AdvSample=adv_sample, dir_name=image_save, quality=quality,
                                                        oriDataset=self.dataset)

                ic_pred = predict(model=self.raw_model, samples=np.array([ic_sample]), device=self.device).detach().cpu().numpy()
                if np.argmax(ic_pred) == np.argmax(self.targets_samples[i]):
                    num_ic += 1

    else:
        for i in range(len(self.adv_samples)):
            if np.argmax(self.softmax_prediction[i]) != np.argmax(self.labels_samples[i]):
                total += 1
                adv_sample = self.adv_samples[i]

                ic_sample = image_compress_transform(IndexAdv=i, AdvSample=adv_sample, dir_name=image_save, quality=quality,
                                                        oriDataset=self.dataset)

                ic_pred = predict(model=self.raw_model, samples=np.array([ic_sample]), device=self.device).detach().cpu().numpy()
                if np.argmax(ic_pred) != np.argmax(self.labels_samples[i]):
                    num_ic += 1
    print('RIC:\t{:.3f}'.format(num_ic / total))
    return num_ic, total, num_ic / total